# Лабораторна робота 2

**Мета:** Розробити інтелектуального агента-машину, що рухається по графу-дорозі з попередньої лабораторної роботи за заданими правилами та метою.  
Отримати практичні навички роботи з інтелектуальними агентами. 

**Завдання:**
1. Отримати навички роботи з інтелектуальними агентами.  
2. Розробити раціонального агента-автомобіль, що рухається по дорозі з попередньої лабораторної роботи.



In [32]:
import matplotlib.pyplot as plt
import networkx as nx
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
from lab1 import RoadGraph


### Клас CarAgent
Модель інтелектуального агента-автомобіля, який рухається по дорожній мережі.
Він приймає рішення на основі евристики Манхеттенської відстані, поступово наближаючись до цілі.


In [33]:
class CarAgent:
    def __init__(self, graph: nx.Graph, start: int, finish: int):
        self.graph = graph
        self.start = start
        self.finish = finish
        self.current_node = start
        self.visited = {start}
        self.history = [start]
        self.positions = nx.get_node_attributes(graph, 'pos')

    def perceive(self):
        return list(self.graph.neighbors(self.current_node))

    def manhattan_distance(self, node1, node2):
        x1, y1 = self.positions[node1]
        x2, y2 = self.positions[node2]
        return abs(x1 - x2) + abs(y1 - y2)

    def decide_next(self):
        neighbors = self.perceive()
        if not neighbors:
            return None
        unvisited = [n for n in neighbors if n not in self.visited]
        if unvisited:
            best_neighbor = min(unvisited, key=lambda n: self.manhattan_distance(n, self.finish))
        else:
            best_neighbor = min(neighbors, key=lambda n: self.manhattan_distance(n, self.finish))
        return best_neighbor

    def move(self):
        next_node = self.decide_next()
        if next_node is not None:
            self.current_node = next_node
            self.visited.add(next_node)
            self.history.append(next_node)

    def get_colors(self):
        colors = []
        for node in self.graph.nodes():
            if node == self.start:
                colors.append("green")
            elif node == self.current_node:
                colors.append("blue")
            elif node == self.finish:
                colors.append("gold")
            elif node in self.visited:
                colors.append("lightgrey")
            else:
                colors.append("white")
        return colors


### Функція draw_graph(agent, ax)
Відображає стан графа з поточним положенням агента і пройденим шляхом.


In [34]:
def draw_graph(agent, ax):
    nx.draw(agent.graph, agent.positions, node_color=agent.get_colors(), with_labels=False, node_size=500, edgecolors="black", linewidths=2, ax=ax)
    path_edges = list(zip(agent.history[:-1], agent.history[1:]))
    nx.draw_networkx_edges(agent.graph, agent.positions, edgelist=path_edges, edge_color="red", width=3, ax=ax)


### Ініціалізація середовища
Створюється дорожня мережа розміром 5×5 із випадковими відсутніми дорогами, а також агент, що рухається від старту до фінішу.


In [35]:
def initialize_environment():
    road = RoadGraph(size=25, remove_edges=10) 
    start, goal = 0, 24
    agent = CarAgent(road.graph, start, goal) 
    
    fig, ax = plt.subplots(figsize=(6, 6))
    return agent, fig, ax


### Функція update(frame)
Оновлює положення агента на кожному кадрі анімації.


In [36]:
def update(frame):
    ax.clear()
    if agent.current_node == agent.finish:
        ani.event_source.stop()
    if frame > 0 and agent.current_node != agent.finish:
        agent.move()
    draw_graph(agent, ax)


### Анімація руху агента
Використовується FuncAnimation для покадрового оновлення положення агента на графі.


In [37]:
agent, fig, ax = initialize_environment()
ani = FuncAnimation(fig, update, frames=range(0, 100), interval=1000, repeat=False)
ani.save('agent_path.gif', writer='imagemagick', fps=10)
HTML(ani.to_jshtml())


![Рух агента](agent_path.gif)

<div style="text-align: right;">

  **Виконав:** Токарюк Станіслав Борисович 
   
  **Перевірив:** Трочун Євгеній Володимирович  
</div>